In [1]:
import os
import sys
KAGGLE_AGENT_PATH = "/kaggle_simulations/agent/"
if os.path.exists(KAGGLE_AGENT_PATH):
    sys.path.insert(0, os.path.join(KAGGLE_AGENT_PATH, 'lib'))
else:
    sys.path.insert(0, os.path.join(os.getcwd(), 'lib'))

In [2]:
from stable_baselines3.common.env_checker import check_env
from environment import KoreGymEnv

env = KoreGymEnv()
check_env(env)

/home/hlz/kaggle/venv/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/hlz/kaggle/kore/lib/stable_baselines3/common/env_checker.py:278: UserWarning: Your action space has dtype float64, we recommend using np.float32 to avoid cast errors.
  warnings.warn(


In [3]:
from stable_baselines3 import PPO
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.monitor import Monitor
from environment import KoreGymEnv

kore_env = KoreGymEnv(config=dict(randomSeed=997269658))  # TODO: This seed is not enough. Seed everything!
monitored_env = Monitor(env=kore_env)
model = PPO('MlpPolicy', monitored_env, verbose=1)

Using cpu device
Wrapping the env in a DummyVecEnv.


In [4]:
model.learn(total_timesteps=5000)

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 399      |
|    ep_rew_mean     | -185     |
| time/              |          |
|    fps             | 33       |
|    iterations      | 1        |
|    time_elapsed    | 60       |
|    total_timesteps | 2048     |
---------------------------------
----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 399        |
|    ep_rew_mean          | 409        |
| time/                   |            |
|    fps                  | 36         |
|    iterations           | 2          |
|    time_elapsed         | 112        |
|    total_timesteps      | 4096       |
| train/                  |            |
|    approx_kl            | 0.00204294 |
|    clip_fraction        | 0.00342    |
|    clip_range           | 0.2        |
|    entropy_loss         | -2.84      |
|    explained_variance   | -0.000137  |
|    learning_rate        | 0.0003     |
|   

In [5]:
# Watch it mercilessly beat the baseline bot - Note: The current episode might not be over yet
kore_env.render(mode="ipython", width=1000, height=800)

In [10]:
model.save(os.path.join("models", "baseline_agent"))

/home/hlz/kaggle/kore/lib/stable_baselines3/common/save_util.py:276: UserWarning: Path 'models' does not exist. Will create it.
  warnings.warn(f"Path '{path.parent}' does not exist. Will create it.")


In [11]:
import numpy as np

# The 'strict' flags sets rewards to 1 if the agent won the episode and 0 else. Useful for evaluation.
eval_env = KoreGymEnv(config=dict(strict=True))  
monitored_env = Monitor(env=eval_env)
model_loaded = PPO.load(os.path.join("models", "baseline_agent"))

model_loaded

In [9]:
def evaluate(model, num_episodes=1):
    """
    Evaluate a RL agent - Adapted from 
    https://colab.research.google.com/github/Stable-Baselines-Team/rl-colab-notebooks/blob/sb3/stable_baselines_getting_started.ipynb
    :param model: (BaseRLModel object) the RL Agent
    :param num_episodes: (int) number of episodes to evaluate it
    :return: (float) Mean reward for the last num_episodes
    """
    all_episode_rewards = []
    for i in range(num_episodes):
        episode_rewards = []
        done = False
        obs = monitored_env.reset()
        while not done:
            action, _ = model.predict(obs)
            obs, _, done, info = monitored_env.step(action)
            if done:
                agent_reward = monitored_env.env.raw_obs.players[0][0]
                opponent_reward = monitored_env.env.raw_obs.players[1][0]
                reward = agent_reward > opponent_reward
            else:
                reward = 0
            # print(reward)
            # monitored_env.render(mode='ipython', height=400, width=300)
            episode_rewards.append(reward)

        all_episode_rewards.append(sum(episode_rewards))

    mean_episode_reward = np.mean(all_episode_rewards)
    print("Mean reward:", mean_episode_reward, "Num episodes:", num_episodes)

    return mean_episode_reward

evaluate(model_loaded, 20)

Mean reward: 0.9 Num episodes: 20


0.9